In [1]:
import json
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
import folium
from folium.plugins import MarkerCluster

In [2]:
#preliminar operations
with open("../geojson/municipi.geojson") as f:
    s_geo=json.load(f)
   
stations = pd.read_csv("../csv/qaria_stazione.csv", sep=';')

milan=folium.Map(location =[45.47,9.2], zoom_start=12, tiles="CartoDB positron")

In [3]:
#set markers
for _, i in stations.iterrows():
    folium.Marker(location=[i['LAT_Y_4326'], i['LONG_X_4326']], popup=str(i['id_amat']), tooltip= "Click for informations").add_to(milan)

In [4]:
def get_geojson_grid(upper_right, lower_left, n=6):
    """Returns a grid of geojson rectangles, and computes the exposure in each section of the grid based on the vessel data.

    Parameters
    ----------
    upper_right: array_like
        The upper right hand corner of "grid of grids" (the default is the upper right hand [lat, lon] of the USA).

    lower_left: array_like
        The lower left hand corner of "grid of grids"  (the default is the lower left hand [lat, lon] of the USA).

    n: integer
        The number of rows/columns in the (n,n) grid.

    Returns
    -------

    list
        List of "geojson style" dictionary objects   
    """

    all_boxes = []

    lat_steps = np.linspace(lower_left[0], upper_right[0], n+1)
    lon_steps = np.linspace(lower_left[1], upper_right[1], n+1)

    lat_stride = lat_steps[1] - lat_steps[0]
    lon_stride = lon_steps[1] - lon_steps[0]

    for lat in lat_steps[:-1]:
        for lon in lon_steps[:-1]:
            # Define dimensions of box in grid
            upper_left = [lon, lat + lat_stride]
            upper_right = [lon + lon_stride, lat + lat_stride]
            lower_right = [lon + lon_stride, lat]
            lower_left = [lon, lat]

            # Define json coordinates for polygon
            coordinates = [
                upper_left,
                upper_right,
                lower_right,
                lower_left,
                upper_left
            ]

            geo_json = {"type": "FeatureCollection",
                        "properties":{
                            "lower_left": lower_left,
                            "upper_right": upper_right
                        },
                        "features":[]}

            grid_feature = {
                "type":"Feature",
                "geometry":{
                    "type":"Polygon",
                    "coordinates": [coordinates],
                }
            }
            
            geo_json["features"].append(grid_feature)

            all_boxes.append(geo_json)

    return all_boxes

In [5]:
#call the function above
lower_left = [45.37867863632306, 9.022178649902344]
upper_right = [45.54555282705949, 9.292030334472656]

grid = get_geojson_grid(upper_right, lower_left , n=50)

In [6]:
#add town councils and the grid (generated with the above function) to milan map
folium.Choropleth(geo_data=s_geo,
                 nan_fill_opacity=None,
                 line_color='black',
                 line_weight=1,
                 line_opacity=1,
                 name=None,
                 overlay=True,
                 control=True,
                 show=True,
                 topojson=None,
                 smooth_factor=None,
                 highlight=None).add_to(milan)


for i, geo_json in enumerate(grid):
    color = plt.cm.Reds(i / len(grid))
    color = mpl.colors.to_hex(color)
    gj = folium.GeoJson(geo_json,
                        style_function=lambda feature, color=color: {
                                                                        'fillColor': color,
                                                                        'color':"black",
                                                                        'weight': 2,
                                                                        'dashArray': '5, 5',
                                                                        'fillOpacity': 0.55,
                                                                    })
    popup = folium.Popup("square {}".format(i))
    gj.add_child(popup)
    milan.add_child(gj)

In [7]:
#print the map
milan